# Advanced Techniques for Entity Resolution and Duplicate Detection
---

## Introduction
In the realm of data management and analysis, ensuring data quality is of paramount importance. Duplicates in datasets can lead to skewed results and erroneous insights. Entity resolution, the process of identifying and consolidating duplicate records that pertain to the same real-world entity, plays a critical role in enhancing data accuracy. This Jupyter notebook delves into advanced techniques for entity resolution and duplicate detection, leveraging Token Blocking and Meta-Blocking methodologies. The notebook follows a structured approach to address the following tasks:

### Task A: Token Blocking for Block Creation
In this task, we explore the concept of Token Blocking, a schema-agnostic approach that facilitates the creation of blocks using Key-Value (K-V) pairs. These K-V pairs represent distinctive Blocking Keys (BKs) derived from entity attribute values. Notably, the identifier column (id) is excluded from the blocking process. By transforming attribute strings to lowercase during token creation, the potential for mismatches is mitigated. The outcome is an index of comprehensively derived BKs. The generated index is meticulously presented using a function designed for clear and readable Key-Value pair visualization.

### Task B: Calculating All Possible Comparisons
Task B is dedicated to computation – we calculate all conceivable comparisons required for resolving duplicates within the blocks established in Task A. By quantifying the final number of comparisons, we gain insights into the computational complexity inherent in the duplicate detection process. This step sets the stage for efficient and accurate entity resolution.

### Task C: Constructing a Meta-Blocking Graph with CBS Weighting
Task C introduces the concept of Meta-Blocking – a strategy involving the creation of a graph based on the block collection crafted in Task A. To enhance the graph's effectiveness, the CBS (Common Block Scheme) Weighting Scheme is employed. Edges with weights below 2 are pruned, streamlining the block collection and minimizing unnecessary comparisons. The revised block collection post pruning serves as the foundation for recalculating the final number of comparisons.

### Task D: Jaccard Similarity Function for Attribute Comparison
The final task introduces a custom function designed for assessing Jaccard similarity between two entities. The attribute "title" is the focus of comparison. Although actual comparisons aren't performed within this notebook, the function serves as an indispensable tool for gauging similarity in attribute values.

Through this comprehensive notebook, readers will gain proficiency in employing advanced techniques for entity resolution and duplicate detection. By leveraging real-world data and following the step-by-step instructions provided, participants will enhance their data manipulation skills and contribute to better data quality and accuracy.

**Note**: This notebook rigorously addresses each task, offering a harmonious blend of meticulous explanations and meticulously crafted code implementations. By actively engaging with the content presented herein, readers will cultivate a profound comprehension of the foundational concepts and intricate techniques that form the bedrock of efficacious entity resolution. 

It is important to underscore that the present notebook constitutes an integral component within the broader landscape of our comprehensive analysis. This notebook is intricately interwoven with the accompanying documentation in PDF format, which provides an expansive contextual framework and supplementary insights to enrich the overall understanding of the complex entity resolution process.

As you navigate through the following sections, each task is elegantly demarcated to facilitate focused exploration. Equipped with both theoretical insights and practical applications, this notebook endeavors to empower readers with the analytical skills necessary to wield advanced techniques in entity resolution adeptly.

**Therefore the contents within this notebook, complemented by the accompanying documentation, synergistically contribute to a holistic and profound grasp of the intricate subject matter at hand.**

*The current analysis will be done on [Jupyter Notebook](http://jupyter.org/) and in [Python 3.10.0](https://www.python.org/downloads/release/python-3100/).*
 
---

> Dimitrios Matsanganis <br />
> Academic ID: f2822212 <br />
> MSc Business Analytics 2022-2023 FT <br />
> Athens University of Economics and Business <br />
> dmatsanganis@gmail.com, dim.matsanganis@aueb.gr

---

---
## Importing Necessary Libraries
---

In this notebook, we will leverage various Python libraries to implement advanced techniques for entity resolution and duplicate detection. Each library has a specific role in enabling us to achieve accurate and efficient results. Below, we list the libraries that will be imported and provide an interpretation of their significance within our analysis. These libraries are essential for Advanced Techniques in Entity Resolution.

1. **Pandas**: Pandas is a fundamental data manipulation library that provides powerful tools for data analysis and preprocessing. We will use it to load and manipulate our dataset, perform attribute transformations, and handle tabular data structures efficiently.

2. **Collections**: The `collections` module provides specialized container datatypes and functions. We will use the `defaultdict` class from this module to create our Meta-Blocking graph more efficiently.


Each of these libraries plays a crucial role in supporting our entity resolution tasks. As we progress through the notebook, we will illustrate how these libraries are employed to implement different techniques and methodologies, contributing to the successful completion of the assignment's tasks.

For this analysis, we will primarily utilize the pandas library, which offers powerful data manipulation capabilities.

In [1]:
# Importing required libraries
import pandas as pd
from collections import defaultdict

---
## Loading the Data
---

Let's start by loading our dataset named `ER-Data.csv`. This dataset contains several columns with entity attributes.

In [2]:
# Import the dataset.
data = pd.read_csv('ER-Data.csv', sep=';')
data.head()

# Display the data.
data.head(10)

id                                           authors  \
0   1                                            QD Inc   
1   2                             AS Argon, JG Hannoosh   
2   3  GH Hansen, LL Wetterberg, H SjÃ¶strÃ¶m, O NorÃ©n   
3   4                    TM Hammett, P Harmon, W Rhodes   
4   5                                        JR Cogdell   
5   6                                        WM Schmidt   
6   7                                          RA Haats   
7   8                          JR Norris, J Deisenhofer   
8   9                                         F Bennour   
9  10                                I Borg, JC Lingoes   

                                       venue    year  \
0                                 San Diego,     NaN   
1                                 Phil. Mag,     NaN   
2                 The Histochemical Journal,  1992.0   
3                                        see     NaN   
4  NEW DIRECTIONS FOR TEACHING AND LEARNING,  1995.0   
5                                         to     NaN   
6                                        NaN  2002.0   
7                       San Diego: Academic,     NaN   
8                 Res. Rep. CERIA, U. Paris,     NaN   
9                                        NaN  1987.0   

                                               title  
0                         11578 Sorrento Valley Road  
1                Initiation of crazes in polystyrene  
2  Immunogold labelling is a quantitative method ...  
3  The Burden of Infectious Disease Among Inmates...  
4  The Role of Faculty Advising in Science and En...  
5  The zero multiplicity of linear recurrence seq...  
6  PREDICITVE VALIDITY OF KINDERGARTEN SCREENERS ...  
7                 The Photosynthetic Reaction Center  
8  F., Diene, AW, Ndiaye, Y. Hachage linÃ©aire Sc...  
9     Multidimensional similarity structure analysis

---
## Data Preprocessing
---

To ensure accurate analysis, we need to preprocess our data. More specifically, before we proceed with token creation and concatenation, it's essential to ensure all our columns have a consistent data type, particularly strings. This step ensures that our operations, like concatenation, proceed without any type-related errors. The following steps will be undertaken:

1. Convert all relevant columns to string type.
2. Handle missing values by replacing them with the string 'None'.

In [3]:
# Convert all relevant columns to string type.
data['authors'] = data['authors'].astype(str)
data['venue'] = data['venue'].astype(str)
data['year'] = data['year'].astype(str)
data['title'] = data['title'].astype(str)

#### Replacing NaN with 'None'

In datasets, missing or undefined values are often represented as NaN (Not a Number). For our analysis and to ensure consistency, we'll replace these NaN values with the string "None".

To be more precise, we decide to replace both actual NaN values and the string `'nan'` with `'None'`.

In [4]:
# Replace NaN values with 'None'.
data = data.fillna('None')

# Replace string 'nan' values with 'None'.
data.replace('nan', 'None', inplace=True)

Executing this code cell should replace both actual NaN values and the string 'nan' with 'None' in our DataFrame.

Lets preview the above change by displaying the data.

In [5]:
# Display the data.
data.head(10)

id                                           authors  \
0   1                                            QD Inc   
1   2                             AS Argon, JG Hannoosh   
2   3  GH Hansen, LL Wetterberg, H SjÃ¶strÃ¶m, O NorÃ©n   
3   4                    TM Hammett, P Harmon, W Rhodes   
4   5                                        JR Cogdell   
5   6                                        WM Schmidt   
6   7                                          RA Haats   
7   8                          JR Norris, J Deisenhofer   
8   9                                         F Bennour   
9  10                                I Borg, JC Lingoes   

                                       venue    year  \
0                                 San Diego,    None   
1                                 Phil. Mag,    None   
2                 The Histochemical Journal,  1992.0   
3                                        see    None   
4  NEW DIRECTIONS FOR TEACHING AND LEARNING,  1995.0   
5                                         to    None   
6                                       None  2002.0   
7                       San Diego: Academic,    None   
8                 Res. Rep. CERIA, U. Paris,    None   
9                                       None  1987.0   

                                               title  
0                         11578 Sorrento Valley Road  
1                Initiation of crazes in polystyrene  
2  Immunogold labelling is a quantitative method ...  
3  The Burden of Infectious Disease Among Inmates...  
4  The Role of Faculty Advising in Science and En...  
5  The zero multiplicity of linear recurrence seq...  
6  PREDICITVE VALIDITY OF KINDERGARTEN SCREENERS ...  
7                 The Photosynthetic Reaction Center  
8  F., Diene, AW, Ndiaye, Y. Hachage linÃ©aire Sc...  
9     Multidimensional similarity structure analysis

---
### Token Creation from Attributes
---

For our analysis, we'll convert **all attribute values to lowercase and split them to create tokens**. 

These tokens will form the basis for our blocking keys.

To be more precise, in this step, we aim to convert all attribute values to lowercase and split them into individual words, resulting in tokens. These tokens are essential components for the blocking method we'll implement later.

In [6]:
# Before transformation.
original_authors = data.authors.copy()
original_year = data.year.copy()
original_venue = data.venue.copy()
original_title = data.title.copy()

# Transforming attributes to tokens.
data.authors = data.authors.str.casefold().str.split()
data.year = data.year.str.casefold().str.split()
data.venue = data.venue.str.casefold().str.split()
data.title = data.title.str.casefold().str.split()

#### Comparing Transformation Results

Let's compare the results before and after the transformation. As an example, we will inspect the title "PREDICITVE VALIDITY OF KINDERGARTEN SCREENERS FOR YOUNG CHILDREN WITH READING DIFFICULTIES" and see how it has been transformed into tokens.

This way we can validate our modifications.

In [7]:
# Identify the row with the mentioned title.
index_of_interest = original_title[original_title == "PREDICITVE VALIDITY OF KINDERGARTEN SCREENERS FOR YOUNG CHILDREN WITH READING DIFFICULTIES"].index[0]

# Display the original and transformed values for comparison.
original_value = original_title[index_of_interest]
transformed_value = data.title[index_of_interest]

original_value, transformed_value

('PREDICITVE VALIDITY OF KINDERGARTEN SCREENERS FOR YOUNG CHILDREN WITH READING DIFFICULTIES',
 ['predicitve',
  'validity',
  'of',
  'kindergarten',
  'screeners',
  'for',
  'young',
  'children',
  'with',
  'reading',
  'difficulties'])

Although the above comparison will help in visually verifying the transformation process, ensuring it's done correctly, lets also display the first 10 rows of the dataset for a more complete visualization. 

You can find the above example under the row 6 and the column title and compare it with the previous display.

In [8]:
# Display the data.
data.head(10)

id                                            authors  \
0   1                                          [qd, inc]   
1   2                         [as, argon,, jg, hannoosh]   
2   3  [gh, hansen,, ll, wetterberg,, h, sjã¶strã¶m,,...   
3   4              [tm, hammett,, p, harmon,, w, rhodes]   
4   5                                      [jr, cogdell]   
5   6                                      [wm, schmidt]   
6   7                                        [ra, haats]   
7   8                      [jr, norris,, j, deisenhofer]   
8   9                                       [f, bennour]   
9  10                            [i, borg,, jc, lingoes]   

                                              venue      year  \
0                                     [san, diego,]    [none]   
1                                     [phil., mag,]    [none]   
2                    [the, histochemical, journal,]  [1992.0]   
3                                             [see]    [none]   
4  [new, directions, for, teaching, and, learning,]  [1995.0]   
5                                              [to]    [none]   
6                                            [none]  [2002.0]   
7                          [san, diego:, academic,]    [none]   
8                  [res., rep., ceria,, u., paris,]    [none]   
9                                            [none]  [1987.0]   

                                               title  
0                    [11578, sorrento, valley, road]  
1          [initiation, of, crazes, in, polystyrene]  
2  [immunogold, labelling, is, a, quantitative, m...  
3  [the, burden, of, infectious, disease, among, ...  
4  [the, role, of, faculty, advising, in, science...  
5  [the, zero, multiplicity, of, linear, recurren...  
6  [predicitve, validity, of, kindergarten, scree...  
7            [the, photosynthetic, reaction, center]  
8  [f.,, diene,, aw,, ndiaye,, y., hachage, linã©...  
9  [multidimensional, similarity, structure, anal...

---
### Concatenating Attributes
---

After tokenizing each of the attributes, our next step is to combine them into a single unified list for each entity. This unified list will serve as a comprehensive set of tokens that encapsulate all the available information about an entity. 

The attributes we have are:

1. **Authors**: This contains the names of authors associated with each entity. It is important as it helps in identifying the creators or contributors of a work.
2. **Venue**: This represents where the work was published or presented. It can be a journal, conference, or any other type of venue.
3. **Year**: The year of publication or presentation. It provides a temporal context to the work.
4. **Title**: The title of the work, which often gives a brief idea about the content or theme of the work.

By concatenating these attributes, we are essentially creating a fingerprint for each entity that will aid in the subsequent blocking process.



In [9]:
# Concatenating the tokenized attributes.
data["tokens"] = data.authors + data.venue + data.year + data.title

#### Outcome of Concatenation


After the concatenation, each entity in our dataset will have a "tokens" column that contains a list of words from all its attributes. This holistic approach ensures that we capture the essence of each entity, increasing the chances of accurate matches in the subsequent steps of our analysis.


In [10]:
# Display the data.
data.head(10)

id                                            authors  \
0   1                                          [qd, inc]   
1   2                         [as, argon,, jg, hannoosh]   
2   3  [gh, hansen,, ll, wetterberg,, h, sjã¶strã¶m,,...   
3   4              [tm, hammett,, p, harmon,, w, rhodes]   
4   5                                      [jr, cogdell]   
5   6                                      [wm, schmidt]   
6   7                                        [ra, haats]   
7   8                      [jr, norris,, j, deisenhofer]   
8   9                                       [f, bennour]   
9  10                            [i, borg,, jc, lingoes]   

                                              venue      year  \
0                                     [san, diego,]    [none]   
1                                     [phil., mag,]    [none]   
2                    [the, histochemical, journal,]  [1992.0]   
3                                             [see]    [none]   
4  [new, directions, for, teaching, and, learning,]  [1995.0]   
5                                              [to]    [none]   
6                                            [none]  [2002.0]   
7                          [san, diego:, academic,]    [none]   
8                  [res., rep., ceria,, u., paris,]    [none]   
9                                            [none]  [1987.0]   

                                               title  \
0                    [11578, sorrento, valley, road]   
1          [initiation, of, crazes, in, polystyrene]   
2  [immunogold, labelling, is, a, quantitative, m...   
3  [the, burden, of, infectious, disease, among, ...   
4  [the, role, of, faculty, advising, in, science...   
5  [the, zero, multiplicity, of, linear, recurren...   
6  [predicitve, validity, of, kindergarten, scree...   
7            [the, photosynthetic, reaction, center]   
8  [f.,, diene,, aw,, ndiaye,, y., hachage, linã©...   
9  [multidimensional, similarity, structure, anal...   

                                              tokens  
0  [qd, inc, san, diego,, none, 11578, sorrento, ...  
1  [as, argon,, jg, hannoosh, phil., mag,, none, ...  
2  [gh, hansen,, ll, wetterberg,, h, sjã¶strã¶m,,...  
3  [tm, hammett,, p, harmon,, w, rhodes, see, non...  
4  [jr, cogdell, new, directions, for, teaching, ...  
5  [wm, schmidt, to, none, the, zero, multiplicit...  
6  [ra, haats, none, 2002.0, predicitve, validity...  
7  [jr, norris,, j, deisenhofer, san, diego:, aca...  
8  [f, bennour, res., rep., ceria,, u., paris,, n...  
9  [i, borg,, jc, lingoes, none, 1987.0, multidim...



By following the above sequence, you can visually understand the importance and outcome of the concatenation process, ensuring that each entity is represented by a comprehensive set of tokens derived from all its available attributes.

---
### Cleaning Tokens
---

As part of our data preprocessing, it's essential to ensure that our tokens are **clean and consistent**. One common issue we might face is the presence of extraneous commas within our tokens, especially after the split operation. These commas can hinder our analysis and matching process, so it's crucial to remove them.

To address this, we'll iterate through each entity's tokens and remove any commas present within them. This iterative process ensures that our final tokens are clean and ready for subsequent analysis.

In [11]:
# Iterate over each entity's tokens.
for i in range(0, len(data)):
    # For each token in the current entity's list of tokens.
    for j in range(0, len(data.tokens[i])):
        # Remove any commas present within the token.
        data.tokens[i][j] = data.tokens[i][j].replace(',', '')

#### Outcome of Token Cleaning

Post this cleaning step, our tokens will be free from unwanted commas, ensuring that each token truly represents a unique word or attribute value. This cleanliness is *vital* for the effectiveness of the token blocking method we'll implement later, as it relies on the **uniqueness** and **consistency** of these tokens.

In [12]:
# Display the data.
data.head(10)

id                                            authors  \
0   1                                          [qd, inc]   
1   2                         [as, argon,, jg, hannoosh]   
2   3  [gh, hansen,, ll, wetterberg,, h, sjã¶strã¶m,,...   
3   4              [tm, hammett,, p, harmon,, w, rhodes]   
4   5                                      [jr, cogdell]   
5   6                                      [wm, schmidt]   
6   7                                        [ra, haats]   
7   8                      [jr, norris,, j, deisenhofer]   
8   9                                       [f, bennour]   
9  10                            [i, borg,, jc, lingoes]   

                                              venue      year  \
0                                     [san, diego,]    [none]   
1                                     [phil., mag,]    [none]   
2                    [the, histochemical, journal,]  [1992.0]   
3                                             [see]    [none]   
4  [new, directions, for, teaching, and, learning,]  [1995.0]   
5                                              [to]    [none]   
6                                            [none]  [2002.0]   
7                          [san, diego:, academic,]    [none]   
8                  [res., rep., ceria,, u., paris,]    [none]   
9                                            [none]  [1987.0]   

                                               title  \
0                    [11578, sorrento, valley, road]   
1          [initiation, of, crazes, in, polystyrene]   
2  [immunogold, labelling, is, a, quantitative, m...   
3  [the, burden, of, infectious, disease, among, ...   
4  [the, role, of, faculty, advising, in, science...   
5  [the, zero, multiplicity, of, linear, recurren...   
6  [predicitve, validity, of, kindergarten, scree...   
7            [the, photosynthetic, reaction, center]   
8  [f.,, diene,, aw,, ndiaye,, y., hachage, linã©...   
9  [multidimensional, similarity, structure, anal...   

                                              tokens  
0  [qd, inc, san, diego, none, 11578, sorrento, v...  
1  [as, argon, jg, hannoosh, phil., mag, none, in...  
2  [gh, hansen, ll, wetterberg, h, sjã¶strã¶m, o,...  
3  [tm, hammett, p, harmon, w, rhodes, see, none,...  
4  [jr, cogdell, new, directions, for, teaching, ...  
5  [wm, schmidt, to, none, the, zero, multiplicit...  
6  [ra, haats, none, 2002.0, predicitve, validity...  
7  [jr, norris, j, deisenhofer, san, diego:, acad...  
8  [f, bennour, res., rep., ceria, u., paris, non...  
9  [i, borg, jc, lingoes, none, 1987.0, multidime...

---
### Final Data Preparation
---

To conclude our data preprocessing, there are two pivotal steps we need to undertake:
1. **Discard** the original attribute columns: Given that we've collated all necessary information into our consolidated `tokens` column, the original columns become redundant.
2. **Reconfigure** the dataframe's index: By setting the `id` column as our index, we streamline our dataframe structure, making entity referencing more intuitive.


In [13]:
# Drop the original attribute columns.
data = data.drop(['authors', 'venue', 'title', 'year'], axis=1)

# Convert the 'id' column to dataframe index.
data = data.set_index('id')

Now, let's take a look at the top 10 rows of our preprocessed data.

In [14]:
# Display the data.
data.head(10)

tokens
id                                                   
1   [qd, inc, san, diego, none, 11578, sorrento, v...
2   [as, argon, jg, hannoosh, phil., mag, none, in...
3   [gh, hansen, ll, wetterberg, h, sjã¶strã¶m, o,...
4   [tm, hammett, p, harmon, w, rhodes, see, none,...
5   [jr, cogdell, new, directions, for, teaching, ...
6   [wm, schmidt, to, none, the, zero, multiplicit...
7   [ra, haats, none, 2002.0, predicitve, validity...
8   [jr, norris, j, deisenhofer, san, diego:, acad...
9   [f, bennour, res., rep., ceria, u., paris, non...
10  [i, borg, jc, lingoes, none, 1987.0, multidime...

With the completion of the meticulous data preprocessing phase, our dataset is now in an optimal state for in-depth analysis. We shall commence our investigative journey with Task A, laying the foundation for subsequent analytical endeavors.

---
## Task A: Creating Blocks using Token Blocking
---

In Task A, we initiate our exploration of advanced entity resolution techniques by delving into the concept of Token Blocking. This innovative methodology facilitates the creation of blocks, forming the foundation for subsequent duplicate detection processes. Token Blocking stands out for its schema-agnostic approach, enabling the utilization of all attributes, except the identifier column (id), to create meaningful blocks. By focusing on attributes and excluding the id column, the resulting blocks capture the distinct attributes that define each entity.

The key idea within Token Blocking is the generation of Key-Value (K-V) pairs, with each entry's key being a unique Blocking Key (BK). These BKs are derived from the entity's attribute values, offering a holistic representation of each entity's characteristics. Importantly, the id column is reserved exclusively for referencing within the blocking index, without participating in the actual block creation process.

To enhance the accuracy of matching, strings are transformed to lowercase during token creation. This strategy helps avoid mismatches that might arise due to differences in case sensitivity. The task culminates with the presentation of the index, achieved through a dedicated function, that displays the Key-Value pairs in a clear and readable format.

In the following sections, we delve into the implementation of Task A, leveraging Python 3.10 and Jupyter Notebook to execute the Token Blocking methodology. By the end of this task, we will have established a solid foundation for subsequent analyses and a deeper understanding of the entity resolution process.

---
### Creating Key-Value Pairs for Tokens
---

In this step, we'll construct a dictionary where each unique token will be a key. The values for each key will be the IDs of the rows where the token is found. 

A crucial aspect to note is that we only want keys with at least 2 values (IDs) to ensure that the token appears in multiple entities, making it relevant for blocking. This approach ensures that we *capture meaningful relationships* between different entities based on common tokens.

In [15]:
# Initialize the dictionary.
kv_pairs = {}

# Iterate over each row in the data.
for i in range(len(data)):
    # Iterate over each token in the tokens column of the current row.
    for key in data.tokens.iloc[i]:
        # Check if the token already exists as a key in the dictionary.
        if key in kv_pairs:
            # Append the ID of the current row to the list of values for the key.
            kv_pairs[key].append(data.index[i])
        else:
            # If the token doesn't exist as a key, create a new key with an empty list as its value.
            kv_pairs[key] = []
            kv_pairs[key].append(data.index[i])

---
### Cleaning the Key-Value Pairs
---

Following the dictionary’s inception, we pivot towards refining it Pruning Redundancies. Certain tokens, while present, don’t contribute meaningfully to our analysis. Specifically, keys resonating with ‘nan’, ‘none’, and blank values were pruned to ensure the cleanliness and relevance of our constructed blocks.

More specifically, after constructing the dictionary, we need to clean it by removing undesirable keys. In this case, we'll remove keys that correspond to `'nan'`, `'none'`, and blank values. These keys don't provide *meaningful information* for blocking and can be considered as noise.

In [16]:
# Remove undesirable keys from the dictionary.
keys_to_remove = ['nan', 'none', '']
for key in keys_to_remove:
    kv_pairs.pop(key, None)

---
### Displaying the Key-Value Pairs
---

With the dictionary structured and refined, our next step orbits around its presentation: Showcasing Interrelationships. We endeavored to present our Key-Value pairs in a manner that was both clear and insightful. Each token, juxtaposed with its associated entities, painted a vivid picture of interlinked relationships, all anchored by shared tokens.

Let's display the resulting key-value pairs. This will show each token and the corresponding entities (represented by IDs) that contain it. Observing this structure gives us an **insight into how entities relate** based on shared tokens, which is the foundation of our blocking method.

In [17]:
# Print the key-value pairs.
for key, values in kv_pairs.items():
    print('Token:', key)
    print('Entities including it:', values)
    print('\n')

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Token: verarbeitung
Entities including it: [3942]


Token: zwei
Entities including it: [3942, 44412]


Token: wahrscheinlichkeitsinformationen
Entities including it: [3942]


Token: [
Entities including it: [3942, 5388, 37822, 63127]


Token: linehan
Entities including it: [3943, 17342, 30003]


Token: keyed
Entities including it: [3943, 54319]


Token: payments
Entities including it: [3943, 41291, 41291, 56673]


Token: (ikp
Entities including it: [3943]


Token: kuok
Entities including it: [3944, 30590, 52986, 64875]


Token: record-quarterly
Entities including it: [3944]


Token: thespecial
Entities including it: [3944]


Token: mâ??mining
Entities including it: [3944]


Token: databasesâ??
Entities including it: [3944, 10093, 18413, 22547, 28682, 31514, 43873, 44238, 48461, 59089, 60508, 60514, 60785, 61386, 61876]


Token: bannon
Entities including it: [3945, 12421, 17664]


Token: nf
Entities including it: [3946, 4676, 7186, 9283, 11140, 18632, 18807, 21454, 22731, 24247, 24307, 

Entities including it: [14624]


Token: sup
Entities including it: [14625, 14625, 23132, 23132, 58451]


Token: 0-d
Entities including it: [14625]


Token: whg
Entities including it: [14626, 17091]


Token: lewin
Entities including it: [14626, 30573, 31381, 39517, 55087, 55087]


Token: banach
Entities including it: [14627, 32713, 34247, 36190, 36190, 39852, 44336, 45627, 46573, 47108, 57602, 58615, 62189]


Token: jeske
Entities including it: [14627, 34247]


Token: retrenchments
Entities including it: [14627, 34247]


Token: defaults
Entities including it: [14627, 15772, 46193]


Token: stronger
Entities including it: [14627, 46384]


Token: dessalles
Entities including it: [14629]


Token: didactic
Entities including it: [14629]


Token: explanations
Entities including it: [14629, 19805, 28861, 32546, 33702, 38170, 39139, 39853, 42945, 44936, 45105, 56961, 57255, 57829, 63109]


Token: itself
Entities including it: [14629, 23294, 23296, 50918, 55938, 64069]


Token: salaria
Entities

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



---
### Conclusion
---

The culmination of Task A signifies a blend of methodical planning intertwined with meticulous execution. The Token Blocking method, augmented by our systematic approach, ensures that we’re poised for success in the subsequent segments of our entity resolution process. Each stage, from token identification to visualization, has been engineered to elevate the accuracy and comprehensiveness of our blocks. 

---
## Task B: Calculating Possible Comparisons
---

In Task B, we embark on a crucial step of the entity resolution process – **Calculating Possible Comparisons**. This phase is integral to understanding the computational complexity inherent in resolving duplicates within the blocks created in Task A. By systematically quantifying the number of comparisons required, we gain insights into the intricacies of duplicate detection and entity consolidation.

**Duplicates** within datasets can obscure meaningful insights and hinder accurate analysis. The process of **entity resolution** entails identifying these duplicates and consolidating them to represent a single real-world entity. This task unveils the mechanics behind evaluating possible comparisons and lays the groundwork for efficient and effective duplicate resolution.

Our methodology involves examining each block crafted in Task A and computing the total number of comparisons needed to identify and merge duplicates within that block. The cumulative count of these comparisons offers a tangible measure of the computational effort required for robust entity resolution. By unveiling the inherent challenges and intricacies, this task underscores the significance of employing advanced techniques for data accuracy.

Let's dive into the code implementation and calculations to shed light on the magnitude of possible comparisons and pave the way for optimal duplicate detection and entity consolidation.

---
### Evaluating Comparisons per Block
---

To accurately calculate the number of comparisons for each block, we need to consider that tokens might be included more than once within a block. This implies that duplicate entities could be appended to some keys, increasing the number of comparisons per block.

We'll follow these steps:

1. Initialize an empty list `comparisons_per_block` to hold the number of comparisons per block.

2. Iterate through each block created in Task A.

3. Calculate the number of entities (n) within the block.

4. Compute the number of comparisons for n entities within the block: `n * (n - 1) / 2`.

5. Append the calculated number of comparisons to the `comparisons_per_block` list.

6. Sum up the list to obtain the total number of comparisons.

Let's implement this methodology in code:

In [18]:
# Initialize an empty list to hold the number of comparisons per block
comparisons_per_block = []

# Iterate through each block
for block_entities in kv_pairs.values():
    # Calculate the number of entities within the block
    num_entities = len(block_entities)
    # Calculate the number of comparisons for n entities within the block
    num_comparisons = num_entities * (num_entities - 1) / 2
    # Append the number of comparisons to the list
    comparisons_per_block.append(num_comparisons)

# Sum up the list to obtain the total number of comparisons
total_comparisons = sum(comparisons_per_block)

---
### Displaying Results
---

Upon executing the provided code, we will obtain the **total number of comparisons** required to effectively resolve duplicates within the blocks that were created as part of *Task A*.

The calculated **number of comparisons** serves as a critical metric to gauge the **computational complexity** associated with the entity resolution process. This information holds paramount importance in shaping strategies to enhance duplicate detection accuracy and streamline entity consolidation.

Let's print the results to gain insights into the scale of computational efforts:

In [19]:
# Display the calculated total number of comparisons
print("The number of total comparisons is:", int(total_comparisons))

The number of total comparisons is: 2644696280


Upon running the code, we will see the output:

**The number of total comparisons is: 2,644,696,280**

This impressive number underscores the intricate nature of duplicate detection and highlights the need for advanced techniques to efficiently navigate the data landscape and ensure data integrity.

---
### Conclusion
---

Entity resolution is a complex task that necessitates meticulous attention to detail. Task B’s emphasis on calculating possible comparisons offers a deep dive into the computational challenges involved in this process. The revelation of over two billion comparisons (2,644,696,280) reiterates the sheer volume and intricacy of data we often grapple with. Such insights fortify the rationale behind employing advanced techniques in entity resolution. By understanding the depth of the challenge, one can appreciate the importance of innovation and advanced methodologies in ensuring data accuracy and integrity in real-world applications. This task not only quantified the challenge but also shed light on the path forward, pushing the boundaries of what’s possible in the realm of entity resolution and duplicate detection.

---
## Task C: Meta-Blocking Graph with CBS Weighting Scheme
---

In this section, we delve into an advanced technique known as **Meta-Blocking**. Building upon the blocks generated in Task A, we aim to further optimize our blocking strategy by:
1. Constructing a graph where nodes represent entities and edges signify that these entities appear in the same block.
2. Leveraging the **CBS Weighting Scheme** to assign weights to the edges, with the weight indicating the number of common blocks shared by the two entities.
3. *Pruning* edges that have a weight of less than 2, ensuring a more streamlined comparison process.
Our overarching goal with this approach is to minimize both the number of duplicates and the volume of non-meaningful comparisons, thereby refining our blocking methodology. Let's embark on this task.

---
### Meta-Blocking Graph with CBS Weighting Scheme
---

**Meta-blocking** is an advanced technique that further optimizes the blocking strategy. By constructing a graph where nodes represent entities and edges signify that these entities appear in the same block, we can enhance the comparison process. The CBS Weighting Scheme allows us to assign weights to the edges, with the weight indicating the number of common blocks shared by the two entities. By pruning edges with a weight less than 2, we can streamline comparisons and potentially reduce false positives.

To be more precise, the **Meta-Blocking Graph Pruning: Algorithm Steps** are presented below: 

1. **Initialize a Dictionary**:
    - We will create a new dictionary named `comparison_dict`.
    - This dictionary will host pairs of entity profiles as IDs. 
    - The key will be a tuple representing the pair of entity profiles.
    - The associated value will be the number of common blocks the two entities share.

2. **Populate the Dictionary with Common Blocks**:
    - For each block in the provided set of blocks:
        - Identify all pairs of entity profiles present in the block.
        - For each pair, increment its corresponding value in `comparison_dict` by one.

3. **Prune the Dictionary**:
    - Retain only those pairs in `comparison_dict` where the edge weight (i.e., the number of common blocks shared) is greater than 2. This ensures that the pair appears in at least two different blocks.

4. **Display Sample Pairs**:
    - Print a few representative pairs of entity profiles that remain after the pruning process. Alongside, display their comparison weights to indicate how many common blocks they share.

5. **Compute the Reduced Computational Cost**:
    - Calculate the total number of comparisons that need to be made after the pruning process.
    - This will help us gauge the reduction in computational cost, emphasizing the most crucial matches.

---
### Initialization and Dictionary Construction
---

Before diving into the Meta-Blocking process, we first initialize a dictionary to store the relationships between entities and their associated weights. This dictionary will be crucial for representing the connections and weights between different entities based on their common blocks.

In other words, we aim to initialize a dictionary to store the relationships between entities and their associated weights. This will be our core data structure to represent connections between entities based on their shared blocks.

In [20]:
# Initialize a dictionary to store the entities and their corresponding weights.
entity_pair_weights = {}

---
### Entity Counter and Loop Control
---

For computational efficiency, we need to limit the number of entities we process. To assist, we'll use:

1. `processed_entities_count`: A counter to track the number of processed entity IDs.
2. `loop_control`: A control variable to halt the loop once we reach our predefined entity limit.

In [21]:
# We will traverse through each block.
# For every entity in a block, we will form pairs with subsequent entities in the same block.
# This ensures we are capturing entities that are part of the same block.

# Entity counter.
processed_entities_count = 0

# Control variable for loop termination.
loop_control = 0

---
### **Constructing Entity Pairs and Weights**
---

The main aim here is to traverse each block (created in the initial blocking step) and identify pairs of entities that co-exist within the same block. This co-existence suggests that these entities might be similar, hence should be compared. The CBS (Common Blocks Scheme) weight represents the number of blocks in which a pair of entities co-exist. This weight will be crucial in later stages to determine if the pair should be considered for comparison.

**The Constructing Entity Pairs and Weights Algorithmic Steps:**


1. **Loop through Blocks:**  
    The process starts by looping through each block. Each block contains entities that were grouped together based on some initial blocking criteria. Think of these entities as potential duplicates or similar records.

2. **Process Each Entity in a Block:**  
    For every entity in the block, the algorithm does several things:
    
    - **Limit Processing:** To ensure efficiency, we may not want to process all entities. So, there's a mechanism to track how many have been processed and to stop after a certain number.
    
    - **Avoid Single Entity Blocks:** Blocks with just one entity are of no use here because we're interested in pairs of entities that appear together. Thus, blocks with a single entity are skipped.

3. **Form Entity Pairs and Update Weights:**  
    The goal here is to identify pairs of entities within each block and keep track of how often each pair occurs across all blocks:
    
    - For every entity in the block, it's paired with every other subsequent entity in the same block.
    - For each pair, we keep track of how many blocks they appear in together. This is done by either initializing a count for new pairs or incrementing the count for existing pairs.

4. **Avoid Redundant Pairing:**  
    After an entity is paired with all other entities in its block, it is removed from the block to prevent repetitive and unnecessary pairing in the next iterations.

5. **Loop Termination:**  
    If a mechanism (like a flag or a counter) indicates that enough entities have been processed, the loop can be terminated early for efficiency.

In [22]:
# Iterate over all blocks to form entity pairs based on shared blocks.
for block in kv_pairs.values():
    for entity in block:
        processed_entities_count += 1
        if processed_entities_count > 100:
            loop_control = 1
            break
        if len(block) <= 1:
            continue
        for i in range(len(block) - 1):
            pair_key_1 = f"{entity},{block[i+1]}"
            pair_key_2 = f"{block[i+1]},{entity}"
            
            # Update the weights for each entity pair.
            if pair_key_1 not in entity_pair_weights and pair_key_2 not in entity_pair_weights:
                entity_pair_weights[pair_key_1] = [1,]
            elif pair_key_2 in entity_pair_weights:
                entity_pair_weights[pair_key_2].append(1)
            else:
                entity_pair_weights[pair_key_1].append(1)
        block.remove(entity)
        if loop_control == 1:
            break

---
### Weight Aggregation
---

In the previous steps, we identified pairs of entities that co-exist within the same blocks. The frequency of their co-existence across multiple blocks is stored as individual counts (in the form of lists of ones). The objective here is to consolidate these counts to determine the total number of blocks in which each entity pair co-exists. This consolidated number serves as the weight of the connection between the two entities in the meta-blocking graph.

**Explanation:**

1. **Why Aggregate Weights?**  
   During the construction of entity pairs, for every block in which an entity pair co-exists, a value of "1" was appended to their corresponding list. This way, if two entities co-existed in 3 blocks, their list would look something like [1, 1, 1]. Aggregating these weights provides a clearer and more concise representation of the data, transforming the list [1, 1, 1] to the integer value 3.


2. **Iterating Through Entity Pairs:**  
    The code iterates through each entity pair in the `entity_pair_weights` dictionary. For each pair the `key` represents the entity pair (e.g., "EntityA,EntityB"), and `values` is the list containing counts of their co-existence in multiple blocks (e.g., [1, 1, 1]).


3. **Summing the Weights:**  
    For each entity pair, the individual counts (ones) are summed up to get the total count:

    ```python
    entity_pair_weights[key] = sum(values)
    ```

    This line of code replaces the list of ones (e.g., [1, 1, 1]) with its sum (e.g., 3) in the `entity_pair_weights` dictionary.


4. **Outcome:**  
    At the end of this step, each entity pair in the `entity_pair_weights` dictionary will have an associated integer weight, representing the total number of blocks they co-exist in. This weight is a crucial factor in determining the strength of the relationship between the two entities in the meta-blocking graph.

In [23]:
# Sum the weights for each entity pair.
for key, values in entity_pair_weights.items():
    entity_pair_weights[key] = sum(values)

# Overview of the entities pairs and weights dictionary that represent the base of the Metablocking Graph Creation.    
print(entity_pair_weights)

{'1,55360': 1, '1,852': 2, '1,923': 2, '1,2857': 2, '1,3057': 2, '1,3486': 1, '1,4378': 2, '1,4854': 1, '1,5589': 1, '1,6339': 1, '1,7038': 1, '1,8574': 1, '1,9368': 1, '1,10500': 1, '1,11596': 1, '1,15004': 2, '1,16358': 1, '1,17005': 1, '1,18337': 1, '1,21912': 1, '1,22216': 2, '1,22275': 2, '1,23987': 1, '1,24308': 2, '1,26475': 2, '1,27244': 1, '1,29327': 1, '1,30987': 2, '1,32596': 2, '1,36256': 1, '1,36411': 1, '1,38590': 1, '1,39000': 2, '1,40028': 1, '1,41393': 1, '1,42111': 1, '1,42685': 1, '1,43073': 2, '1,43918': 2, '1,44647': 1, '1,44908': 2, '1,45497': 2, '1,46763': 2, '1,47124': 2, '1,49406': 2, '1,50987': 2, '1,51988': 2, '1,52505': 2, '1,53149': 2, '1,56545': 1, '1,56805': 2, '1,57323': 2, '1,58857': 2, '1,59169': 1, '1,60213': 1, '1,61288': 1, '1,61397': 1, '1,62978': 1, '1,65238': 1, '923,923': 1, '923,2857': 2, '923,3057': 2, '923,3486': 1, '923,4378': 2, '923,4854': 1, '923,5589': 1, '923,6339': 1, '923,7038': 1, '923,8574': 1, '923,9368': 1, '923,10500': 1, '923,11

---
### Pruning Entity Pairs
---

The primary goal of this step is to retain only those entity pairs that have a high likelihood of being genuine matches. This is done by pruning pairs based on their associated weights. The weight represents the number of blocks in which a pair of entities co-exist. A higher weight indicates that the entities frequently appear together, suggesting they might be similar or even duplicates.

**Explanation:**

1. **Why Prune?**  
   Pruning is a crucial optimization step. By removing entity pairs with low weights, we reduce the number of potential comparisons in subsequent steps. This not only speeds up the process but also reduces the chances of false positives (erroneously identifying non-matching entities as matches).


2. **The Pruning Criterion:**  
   The chosen criterion here is a weight threshold. Entity pairs with a weight less than or equal to 2 are considered to have a weak association and are thus pruned.

   ```python
   if value > 2
   ```

   This implies that if two entities appear together in only one or two blocks, their association might be coincidental. However, if they appear together in three or more blocks, their association is considered stronger, and they are retained for further processing.


3. **Python Dictionary Comprehension:**  
   The pruning process leverages Python's dictionary comprehension. This allows us to iterate over the original `entity_pair_weights` dictionary and create a new dictionary (`pruned_entity_pair_weights`) that contains only the pairs meeting our criterion.

   ```python
   pruned_entity_pair_weights = {key: value for key, value in entity_pair_weights.items() if value > 2}
   ```

   In this line, for each `key-value` pair in `entity_pair_weights`, if the value (weight) is greater than 2, the pair is included in the `pruned_entity_pair_weights`.


4. **Outcome:**  
   After this step, the `pruned_entity_pair_weights` dictionary contains a subset of the original entity pairs. These retained pairs are considered to have a stronger association based on their co-existence across multiple blocks. They will be the primary focus in subsequent comparison or matching processes.

In [24]:
# Filter out entity pairs with a weight less than 2.
pruned_entity_pair_weights = {key: value for key, value in entity_pair_weights.items() if value > 2}

---
### Displaying Filtered Entity Pairs
---


After pruning, it's beneficial to visualize some of the entity pairs to get an insight into the data. The code aims to display the first few (in this case, 5) entity pairs that have a weight indicating they share 2 or more common blocks. 

**Displaying Filtered Entity Pairs Procedure Steps:**

1. **Initialization:**  
   A counter is initialized to keep track of how many pairs have been printed. The aim is to limit the output to a manageable number (5 in this instance).

In [25]:
counter = 0

2. **Iterate and Display:**  
   The code iterates over the `pruned_entity_pair_weights` dictionary, which contains entity pairs that have been pruned based on their weights.
   
    For each pair:
    - The entities (Nodes) and their shared number of blocks (Number of Common Blocks) are printed.
    - The counter is incremented.
    - The loop breaks after printing 5 pairs.

In [26]:
for key,values in pruned_entity_pair_weights.items():
    if counter < 5:
        print('Nodes:',key,'\n' 'Number of Common Blocks:',values,'\n')
        counter+=1

Nodes: 1,29089 
Number of Common Blocks: 3 

Nodes: 11,29089 
Number of Common Blocks: 3 

Nodes: 215,29089 
Number of Common Blocks: 3 

Nodes: 352,29089 
Number of Common Blocks: 3 

Nodes: 496,29089 
Number of Common Blocks: 3 



---
### Calculating Total Comparisons After Pruning
---

Once the pruning process is complete, it's important to understand how much the computational burden has been reduced. This step calculates the total number of entity comparisons that are still required after pruning. By doing so, we can gauge the efficiency gains achieved through the meta-blocking process.

**Explanation:**

1. **Why Calculate Total Comparisons?**  
   The initial blocking process groups entities into blocks, with each block containing potential matches. Without any optimization, the number of comparisons can be substantial. The meta-blocking process, especially pruning, aims to reduce this number. Calculating the total comparisons post-pruning provides insights into:
   
   - The effectiveness of the meta-blocking process.
   - The computational effort required in subsequent matching processes.


2. **Summing the Weights:**  
   The weights in the `pruned_entity_pair_weights` dictionary represent the number of blocks in which each entity pair co-exists. After pruning, this weight also indicates the number of comparisons needed for each pair. 

In [27]:
# Calculate the total number of comparisons after pruning.
total_comparisons_after_pruning = sum(pruned_entity_pair_weights.values())

    By summing all these weights (values in the dictionary), we get the total number of comparisons required post-pruning. The Python `sum()` function makes this aggregation straightforward.


3. **Displaying the Result:**  
   Presenting the result provides a clear picture of the computational savings:

In [28]:
print(f'The number of total comparisons after pruning is: {total_comparisons_after_pruning}')

The number of total comparisons after pruning is: 207


### Interpreting Total Comparisons After Pruning

Given the result:
> **The number of total comparisons is: 207**

This means that after the entire meta-blocking process, including the pruning based on the CBS (Common Blocks Scheme) weighting scheme, we are left with 207 entity-to-entity comparisons that need to be made.

---
### Conclusion
---

**Task C** embarked on the intricate journey of constructing a Meta-Blocking graph from the block collection established in **Task A**. By leveraging the CBS Weighting Scheme, we not only identified the commonalities between entities but also streamlined the comparison process through strategic pruning.

The results from **Task B** unveiled a whopping **2.6 billion** comparisons, underscoring the sheer volume and complexity of data we initially grappled with. Such a colossal number magnified the challenges inherent in the entity resolution process, highlighting the pressing need for further optimization.

Against this backdrop, **Task C** introduced a refined approach. The Meta-Blocking graph, by its very design, accentuated the relationships between entities based on their shared blocks. By assigning weights to these relationships using the CBS scheme, we were able to discern the strength and significance of each potential match.

However, the game-changer was the pruning strategy. By judiciously eliminating edges with a weight of less than 2, we not only reduced the computational burden but also honed in on the most promising entity pairs. This pruning not only streamlined the comparison process but also set the stage for enhanced accuracy in subsequent entity resolution steps.

Re-calculating the number of comparisons post-pruning, as done in **Task B**, provided a tangible metric of our efficiency gains. This re-evaluation, when juxtaposed with the initial 2.6 billion comparisons, served as a testament to the **effectiveness of the meta-blocking approach**. 

In essence, **Task C** built upon the foundation laid by **Task A** and the insights gleaned from **Task B**. By introducing advanced techniques like meta-blocking and pruning, we navigated the intricate landscape of entity resolution with increased finesse and efficiency. The task not only underscored the challenges of handling voluminous data but also showcased the transformative potential of innovative methodologies in ensuring data accuracy and integrity.

---
## Task D: Jaccard Similarity Function
---


In the final stage of the Token Blocking method, we delve into the intricate task of computing similarity scores between entity profiles. The primary objective here is to ascertain whether two entities can be deemed as identical based on their similarity scores. This would imply that the entities correspond to the same real-world object.

### Steps for Actual Comparison Calculations:

1. **Attribute Selection**: Decide upon the attributes that will serve as the foundation for the calculation of similarity between the two entity profiles. The selection of attributes is pivotal as it will influence the accuracy of the similarity score.
  
2. **Selecting an Appropriate Similarity Metric**: Depending on the nature of the attribute values, an appropriate similarity metric should be chosen:
   - **Strings**: Use measures like the Heinz distance.
   - **Sets**: Use measures like the Jaccard Similarity.
   - **Vectors**: Opt for the cosine similarity, etc.

3. **Structuring the Problem**: Before crafting the function to compute similarities, it's imperative to decide on its inputs. Will it be the entire dataset or distinct entities? Also, in what format will the data be provided? 

### Our Chosen Approach:

For this exercise, we are narrowing our focus to a subset of the initial dataset post-tokenization of each column/attribute. Here, each attribute manifests as a set of tokens. Rather than incorporating all attributes, we will base our similarity calculations on a singular attribute. The metric of choice will be the **Jaccard Similarity**.

#### Jaccard Similarity:

Given two sets, \( A \) and \( B \), the Jaccard Similarity \( J(A, B) \) is computed as:

\[
J(A, B) = \frac{|A \cap B|}{|A \cup B|}
\]

Where \( |A \cap B| \) represents the size of the intersection of the sets \( A \) and \( B \), and \( |A \cup B| \) is the size of the union of the sets.

In [29]:
data.sample(10)

tokens
id                                                      
25819  [ne, grulke, &hellip;, d, (tech., comp.), proc...
26230  [a, el, abbadi, s, toueg, acm, transactions, o...
59491  [ks, vallerio, nk, jha, none, none, task, grap...
26423  [tm, donovan, stanford, university, technical,...
59878  [oa, bamgboyã©, none, none, writings, on, tech...
39495  [rt, ng, g, han, proceedings, of, the, 20th, v...
49139  [r, hartrey, i, kestin, journal, of, emergency...
55915  [c, ansi, bt, technology, journal, 1997.0, ope...
17849  [pr, brown, rf, elmore, none, 1982.0, analyzin...
2963   [s, terdemanâ?¦, pc, magazine, september, none...